In [12]:
from pathlib import Path
from label_studio_sdk.client import LabelStudio
from label_studio_sdk.core import ApiError
from fishsense_api_sdk.client import Client
import asyncio
from tqdm.asyncio import tqdm_asyncio
from tqdm.notebook import tqdm
import json
from fishsense_api_sdk.models.laser_label import LaserLabel

In [2]:
URL = "http://localhost:8000"

In [3]:
label_studio_api_key = Path("..") / ".label_studio_api_key"

label_studio_api_key.exists()

True

In [4]:
ls = LabelStudio(base_url=f"https://labeler.e4e.ucsd.edu", api_key=label_studio_api_key.read_text().strip())

In [5]:
async with Client(URL) as fs:
    dives = await fs.dives.get()

len(dives), dives[0]

(479,
 Dive(id=21, name='H slate dive 1', path='2023.08.03.FishSense.FSL-01D/H slate dive 1', dive_datetime=datetime.datetime(2023, 8, 3, 9, 11, 50, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=None, camera_id=1, dive_slate_id=None))

In [6]:
async with Client(URL) as fs:
    laser_labels = await tqdm_asyncio.gather(*[fs.labels.get_laser_labels(dive.id) for dive in dives])
    laser_labels = [label for sublist in laser_labels for label in sublist]

len(laser_labels), laser_labels[0]

100%|██████████| 479/479 [00:22<00:00, 21.10it/s]


(44563,
 LaserLabel(id=26762, label_studio_task_id=34074, label_studio_project_id=10, x=1918.7821683613638, y=1290.050424459971, label='Red Laser', updated_at=datetime.datetime(2024, 11, 20, 15, 3, 48, 350068, tzinfo=TzInfo(0)), superseded=False, completed=True, label_studio_json={'id': 34074, 'annotations': [{'id': 9302, 'completed_by': 11, 'result': [{'id': '3BhMgb1eO5', 'type': 'keypointlabels', 'value': {'x': 48.12596359070388, 'y': 42.77355518766482, 'width': 0.1701818875349385, 'keypointlabels': ['Red Laser']}, 'origin': 'manual', 'to_name': 'img-1', 'from_name': 'kp-1', 'image_rotation': 0, 'original_width': 3987, 'original_height': 3016}], 'was_cancelled': False, 'ground_truth': False, 'created_at': '2024-11-20T15:03:48.297461Z', 'updated_at': '2024-11-20T15:03:48.297474Z', 'draft_created_at': None, 'lead_time': 21.938, 'prediction': {}, 'result_count': 0, 'unique_id': '5b470693-2b55-4f14-8db8-b05d10a9d070', 'import_id': None, 'last_action': None, 'task': 34074, 'project': 10, 

In [7]:
label_studio_project_ids = list({label.label_studio_project_id for label in laser_labels if label.label_studio_project_id is not None})

len(label_studio_project_ids), label_studio_project_ids

(10, [10, 43, 42, 57, 58, 59, 60, 61, 62, 63])

In [8]:
tasks = []

for project_id in tqdm(label_studio_project_ids):
    try:
        project = ls.projects.get(project_id)
    except ApiError as e:
        print(f"Error fetching project {project_id}: {e}")
        continue

    tasks += list(ls.tasks.list(project=project_id))

len(tasks), tasks[0]

  0%|          | 0/10 [00:00<?, ?it/s]

Error fetching project 10: status_code: 404, body: {'id': 'dcc6381f-71b7-4f52-ad86-816bce05bcd0', 'status_code': 404, 'version': '1.21.0', 'detail': 'No Project matches the given query.', 'exc_info': None}


(30019,
 LseTask(agreement=None, agreement_selected=None, annotations=[{'id': 92210, 'result': [{'id': 'ieVgIKA91P', 'type': 'keypointlabels', 'value': {'x': 49.00506942030147, 'y': 43.05559796746316, 'width': 0.2757321850587165, 'keypointlabels': ['Red Laser']}, 'origin': 'manual', 'to_name': 'img-1', 'from_name': 'kp-1', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}], 'created_username': 'Kshitij Khandagale kshitijkhandagale2007@gmail.com, 131', 'created_ago': '6\xa0months', 'completed_by': 131, 'was_cancelled': False, 'ground_truth': False, 'created_at': '2025-05-21T18:03:55.312289Z', 'updated_at': '2025-05-21T18:03:55.312310Z', 'draft_created_at': '2025-05-21T18:03:53.038156Z', 'lead_time': 52.045, 'import_id': None, 'last_action': None, 'bulk_created': False, 'task': 190321, 'project': 43, 'updated_by': 131, 'parent_prediction': None, 'parent_annotation': None, 'last_created_by': None}], annotations_ids='92210', annotations_results='[{id:ieVgIKA91P, type:ke

In [9]:
label_studio_task_to_laser_label_map = {
    label.label_studio_task_id: label
    for label in laser_labels
}

len(label_studio_task_to_laser_label_map)

44563

In [16]:
LASER_LABEL_KEY_NAMES = ["kp-1", "laser"]

coroutines = []
async with Client(URL) as fs:
    for task in tqdm(tasks):
        laser_label: LaserLabel = label_studio_task_to_laser_label_map.get(task.id)

        if laser_label is None:
            continue

        email = task.annotations[0]["created_username"].split(",")[0].split(' ')[-1].strip()
        tqdm.write(f"Processing task {task.id} for user {email}")
        user = await fs.users.get(email=email)

        laser_label.label_studio_json = json.loads(task.json())
        laser_label.user_id = user.id
        laser_label.completed = task.is_labeled

        if len(task.annotations) > 0:
            for laser_label_key in LASER_LABEL_KEY_NAMES:
                    laser_label_section = [r for r in task.annotations[0]["result"] if r["from_name"] == laser_label_key]
                    laser_label_section = laser_label_section[0] if len(laser_label_section) > 0 else None

                    if laser_label_section is not None:
                        break

            if laser_label_section is not None:
                original_width = laser_label_section["original_width"]
                original_height = laser_label_section["original_height"]

                laser_x = int(
                    round(laser_label_section["value"]["x"] * original_width / 100)
                )
                laser_y = int(
                    round(
                        laser_label_section["value"]["y"] * original_height / 100
                    )
                )
                laser_label_str = laser_label_section["value"]["keypointlabels"][0]

                laser_label.x = laser_x
                laser_label.y = laser_y
                laser_label.label = laser_label_str
        
        coroutines.append(fs.labels.put_laser_label(laser_label.image_id, laser_label))

    await tqdm_asyncio.gather(*coroutines)

/tmp/ipykernel_177007/1762946115.py:3: RuntimeWarning: coroutine 'LabelClient.put_laser_label' was never awaited
  coroutines = []


  0%|          | 0/30019 [00:00<?, ?it/s]

/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 92210, 'result': ...last_created_by': None}], input_type=list])
  serialized = handler(self)


Processing task 190321 for user kshitijkhandagale2007@gmail.com
Processing task 190322 for user kshitijkhandagale2007@gmail.com


/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 92212, 'result': ...last_created_by': None}], input_type=list])
  serialized = handler(self)
/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 92215, 'result': ...last_created_by': None}], input_type=list])
  serialized = handler(self)


...

/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 121789, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)
/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 122095, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)


Processing task 223618 for user alli@reef.org
Processing task 223619 for user alli@reef.org


/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 122096, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)
/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 122097, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)


Processing task 223620 for user alli@reef.org


100%|██████████| 8249/8249 [03:22<00:00, 40.78it/s]


In [ ]:
task.annotations[0]

{'id': 92244,
 'result': [{'id': 'OxMnhyQNIM',
   'type': 'keypointlabels',
   'value': {'x': 49.782107412237295,
    'y': 45.45019086865212,
    'width': 0.2757321850587165,
    'keypointlabels': ['Red Laser']},
   'origin': 'manual',
   'to_name': 'img-1',
   'from_name': 'kp-1',
   'image_rotation': 0,
   'original_width': 4014,
   'original_height': 3016}],
 'created_username': 'Kshitij Khandagale kshitijkhandagale2007@gmail.com, 131',
 'created_ago': '6\xa0months',
 'completed_by': 131,
 'was_cancelled': False,
 'ground_truth': False,
 'created_at': '2025-05-21T18:13:54.308927Z',
 'updated_at': '2025-05-21T18:13:54.308943Z',
 'draft_created_at': None,
 'lead_time': 20.538,
 'import_id': None,
 'last_action': None,
 'bulk_created': False,
 'task': 190343,
 'project': 43,
 'updated_by': 131,
 'parent_prediction': None,
 'parent_annotation': None,
 'last_created_by': None}

In [ ]:

laser_label_section = [r for r in task.annotations[0]["result"] if r["from_name"] == "laser"]
laser_label_section = laser_label_section[0] if len(laser_label_section) > 0 else None

laser_label_section